In [1]:
import pandas as pd
from wtpsplit.utils import Constants

In [2]:
# set print options
pd.set_option("display.max_columns", 500)
pd.set_option("display.width", 10000)
pd.set_option("max_colwidth", 300)

In [3]:
lyrics_distinct_all = pd.read_json("data/lyrics_distinct_markus_frohmann.json.bz2", lines=True)

In [4]:
lyrics_distinct_all.shape

(1279204, 11)

In [5]:
lyrics_distinct_all.head()

_id                                                                                                                                                                                                                                                                                                       lyrics lyrics_language                                                                                                                                                                                                                                                                                             lyrics_sanitized lyrics_sanitized_lang                                  track                        artist                                                                                                                      tags_lfm                  micro_genres_lfm primary_tag_genius                     all_tags_genius
0   4500284  !\nA A\nTriple A!\n(Triple A?)\nA! A! A!\nU can B 1\nU can B 1 2\n2 B or not 2 B\nC?\nABC R E Z\nABC R fun\nA!\nAlphabetical order\n\nHere we go...\nUFO on LSD\nR2D2, C3P0, how 'bout ET?\nABC, BBC, CBN, NBC\nMTV, VH1, HBO, CNN\nSCTV, SAT\nDegree? BA, BN, BS, A! How about BAC? A!\nAlphabetical or...              en  !\nA A\nTriple A!\n(Triple A?)\nA! A! A!\nU can B 1\nU can B 1 2\n2 B or not 2 B\nC?\nABC R E Z\nABC R fun\nA!\nAlphabetical order\n\nHere we go...\nUFO on LSD\nR2D2, C3P0, how 'bout ET?\nABC, BBC, CBN, NBC\nMTV, VH1, HBO, CNN\nSCTV, SAT\nDegree? BA, BN, BS, A! How about BAC? A!\nAlphabetical or...                    en                     Alphabetical Order                     Joe Walsh                                                  {'rock': 100, 'Joe Walsh': 100, 'rock alternativo': 100, 'alltimefavs': 100}                     {'rock': 100}                pop  {'primary': 'pop', 'all': ['pop']}
1   6999031  !\nI've been looking\nI've been searching\nI've been seeking\nBut I can't find love\n\nI've been driving endless hours\nThere's nothing doing\nI can't find love\nOn cold mornings\nSun drenched evenings\nThrough restless dreamings\nEverywhere\nIn the papers\nOn those talk-back television shows\nA...              en  !\nI've been looking\nI've been searching\nI've been seeking\nBut I can't find love\n\nI've been driving endless hours\nThere's nothing doing\nI can't find love\nOn cold mornings\nSun drenched evenings\nThrough restless dreamings\nEverywhere\nIn the papers\nOn those talk-back television shows\nA...                    en                              Black Ice  My Friend The Chocolate Cake                                                                                                        {'8 of 10 stars': 100}                               NaN                pop  {'primary': 'pop', 'all': ['pop']}
2  45963513  !\nYou come on like a dream, peaches and cream\nLips like strawberry wine\nYou're sixteen, you're beautiful and you're mine\n\nYou're all ribbons and curls, ooh what a girl\nEyes that sparkle and shine\nYou're sixteen, you're beautiful and you're mine\n\nYou're my baby, you're my pet\nWe fell in...              en  !\nYou come on like a dream, peaches and cream\nLips like strawberry wine\nYou're sixteen, you're beautiful and you're mine\n\nYou're all ribbons and curls, ooh what a girl\nEyes that sparkle and shine\nYou're sixteen, you're beautiful and you're mine\n\nYou're my baby, you're my pet\nWe fell in...                    en  You're Sixteen (Original Hit Version)               Johnny Burnette                                                                                      {'pop': 100, '60s': 100, '40s-50s': 100}                      {'pop': 100}                pop  {'primary': 'pop', 'all': ['pop']}
3  13614982  !! -- Guitar Intro -- !!\n\nYou know that this smile\nTo go deep in my life baby\nI was born to fly\nOver this ocean darlin'\n\nMaybe we can try\nSomeday not later darlin'\nI learned another rhythm\nThats over my soul\n\nAnd darling hes in town\nAre y

In [6]:
lyrics_distinct_all["lyrics_sanitized_lang"].value_counts()

lyrics_sanitized_lang
en         1278136
ko             100
fr              93
es              88
de              65
            ...   
zh_Hant          1
ve               1
ss               1
br               1
xx_Qaai          1
Name: count, Length: 101, dtype: int64

In [7]:
lyrics_distinct_all["primary_tag_genius"].value_counts()

primary_tag_genius
pop                   734241
rock                  327013
rap                   129445
r-b                    38821
country                36069
non-music              13376
denmark                  228
varnell-15-16-12th        11
Name: count, dtype: int64

In [8]:
from lingua import Language, LanguageDetectorBuilder

detector = (
    LanguageDetectorBuilder.from_all_languages()
    .with_preloaded_language_models()
    .with_minimum_relative_distance(0.9)
    .build()
)

In [9]:
result = detector.detect_languages_in_parallel_of(
    [
        "Too big, too small\nSize does matter, after all\nZu groß, zu klein\nEr könnte etwas größer sein\nMercedes Benz und Autobahn\nAlleine in das Ausland fahren\nReise Reise",
        "Fahrvergnügen\nIch will nur Spaß, mich nicht verlieben\n\n[Pre-Refrain]\nJust a little bi",
    ]
)
print(result)

[Language.GERMAN, Language.GERMAN]


In [10]:
result[0].iso_code_639_1.name.lower()

'de'

In [11]:
from tqdm import tqdm

tqdm.pandas()

# feed in multiple lyrics at once
lyrics_sanitized_lang_lingua = []
# use 100 chunks at a time
for i in tqdm(range(0, len(lyrics_distinct_all), 100)):
    lyrics_sanitized_lang_lingua.extend(
        detector.detect_languages_in_parallel_of(lyrics_distinct_all["lyrics_sanitized"].iloc[i : i + 100])
    )

100%|██████████| 12793/12793 [05:40<00:00, 37.63it/s] 


In [12]:
lyrics_distinct_all["lyrics_sanitized_lang_lingua"] = [
    x.iso_code_639_1.name.lower() if x else None for x in lyrics_sanitized_lang_lingua
]

In [13]:
lyrics_distinct_all["lyrics_sanitized_lang_lingua"].value_counts(dropna=False)

lyrics_sanitized_lang_lingua
en      1252790
None      19875
yo          896
de          679
fr          623
es          559
sn          461
la          386
ja          354
tl          304
ko          274
it          256
fi          166
sw          150
pt          130
nl          121
cy          116
sv          101
nb           95
pl           88
st           87
id           59
so           49
da           46
ga           40
et           39
zu           37
zh           36
eu           34
ts           33
hr           30
is           27
xh           26
eo           24
mi           21
tn           19
sq           19
sl           16
tr           16
nn           14
hu           13
vi           12
af           12
ca           11
sk           11
cs           11
bs           10
ms           10
ro            5
lt            4
lv            2
lg            2
ru            2
he            1
az            1
ar            1
Name: count, dtype: int64

In [14]:
lyrics_distinct_all.loc[(lyrics_distinct_all["primary_tag_genius"] == "denmark")]  # ["lyrics_sanitized_lang"]

_id                                                                                                                                                                                                                                                                                                       lyrics lyrics_language                                                                                                                                                                                                                                                                                             lyrics_sanitized lyrics_sanitized_lang                              track         artist                                                                                                                                                                                                          tags_lfm                                                                micro_genres_lfm primary_tag_genius                                                                                                                      all_tags_genius lyrics_sanitized_lang_lingua
4407     16933435  [Produced by WZRD]\n\n"Now certainly, we all recognize the extremely, extremely low probability of life existing on the moon."\n\n[Intro]\nHmm, hmm, alright\nHmm, hmm, hmm\n\n[Verse 1]\nDrinking again, drinking again\nBottles up, I'm in it to win\nWith none of my friends, just me and this bottle...              en  "Now certainly, we all recognize the extremely, extremely low probability of life existing on the moon."\n\nHmm, hmm, alright\nHmm, hmm, hmm\n\nDrinking again, drinking again\nBottles up, I'm in it to win\nWith none of my friends, just me and this bottle\nPeople say that I'm off, say that I'm of...                    en              Going to the Ceremony       Kid Cudi  {'Hip-Hop': 100, 'electronic': 100, 'hip hop': 67, 'rock': 67, 'alternative rock': 34, 'american': 34, 'alternative hip-hop': 34, '10s': 34, 'alternative hip hop': 34, 'kid cudi': 34, 'its all happening': 34}  {'hip hop': 67, 'rock': 67, 'alternative rock': 34, 'alternative hip hop': 34}            denmark  {'primary': 'denmark', 'all': ['denmark', 'denmark', 'denmark', 'denmark', 'rap', 'alternative-rock', 'space-rock', 'rock', 'rap']}                           en
12368    35844478  (Check this out, DJ E-V)\n\n[Verse]\nHeeey, she say I'm different\nI'm zoned like, how bitch?\nShe say, I dress cool\nAnd cause my accent\nOh shit, this girl must want a nut\nI'mma jizz up in her face\nWhile I'm palming the butt\nDidn't do my struck, cowboy mid-western\nShe did it all for me, no...              en  (Check this out, DJ E-V)\n\nHeeey, she say I'm different\nI'm zoned like, how bitch?\nShe say, I dress cool\nAnd cause my accent\nOh shit, this girl must want a nut\nI'mma jizz up in her face\nWhile I'm palming the butt\nDidn't do my struck, cowboy mid-western\nShe did it all for me, now it's he...                    en               Skit - Foggy Glasses       Kid Cudi                                                                                                                                                                                                 {'vugube62': 100}                                                                             NaN            denmark                                                                  {'primary': 'denmark', 'all': ['denmark', 'denmark', 'rap', 'rap']}                           en
17811    42985758  [Intro]\n(If young Metro don't trust you, I'm gon' shoot you)\n\n[Chorus]\nRemember feelin' broke as fuck (Yeah)\nBut now I'm pullin' up in Rover trucks (I'm pullin' up in Rover trucks now)\nRemember these bitches ain't wanna fuck\nNow she give me head outside of Toys"R"Us (These bitches suck an...              en  (If young Metro don't trust you, I'm gon' shoot you)\n\nRemember feelin' broke as fuck (Yeah)\nBut now I'm pullin' up in Rover trucks (I'm pu

In [15]:
# drop NaN values
lyrics_distinct_all = lyrics_distinct_all.dropna(subset=["lyrics_sanitized_lang_lingua"])

## Set up different Versions

### Lower

In [16]:
lyrics_distinct_all["lyrics_sanitized_lower"] = lyrics_distinct_all["lyrics_sanitized"].str.lower()

## Non-punctuated

In [17]:
# use Constants.PUNCTUATION_CHARS to remove all punctuation from lyrics_sanitized
# for each char separately


def remove_punctuation(text):
    for punct in Constants.PUNCTUATION_CHARS:
        text = text.replace(punct, "")
    return text


lyrics_distinct_all["lyrics_sanitized_rmp"] = lyrics_distinct_all["lyrics_sanitized"].progress_apply(remove_punctuation)
lyrics_distinct_all["lyrics_sanitized_lower_rmp"] = lyrics_distinct_all["lyrics_sanitized_rmp"].str.lower()

100%|██████████| 1259329/1259329 [04:24<00:00, 4757.54it/s] 


# Segment

In [18]:
lyrics_distinct_all["verses"] = lyrics_distinct_all["lyrics_sanitized"].str.split("\n\n")
# lower
lyrics_distinct_all["verses_lower"] = lyrics_distinct_all["lyrics_sanitized_lower"].str.split("\n\n")
# remove punctuation
lyrics_distinct_all["verses_rmp"] = lyrics_distinct_all["lyrics_sanitized_rmp"].str.split("\n\n")
lyrics_distinct_all["verses_lower_rmp"] = lyrics_distinct_all["lyrics_sanitized_lower_rmp"].str.split("\n\n")

In [19]:
# remove \n from within verses


def strip_n(verse, lang):
    replace = Constants.SEPARATORS[lang]
    return verse.replace("\n", replace)


lyrics_distinct_all["verses_strip_n"] = lyrics_distinct_all.progress_apply(
    lambda x: [strip_n(verse, x["lyrics_sanitized_lang_lingua"]) for verse in x["verses"]],
    axis=1,
)
# lower
lyrics_distinct_all["verses_lower_strip_n"] = lyrics_distinct_all.progress_apply(
    lambda x: [strip_n(verse, x["lyrics_sanitized_lang_lingua"]) for verse in x["verses_lower"]],
    axis=1,
)
# remove punctuation
lyrics_distinct_all["verses_rmp_strip_n"] = lyrics_distinct_all.progress_apply(
    lambda x: [strip_n(verse, x["lyrics_sanitized_lang_lingua"]) for verse in x["verses_rmp"]],
    axis=1,
)
lyrics_distinct_all["verses_lower_rmp_strip_n"] = lyrics_distinct_all.progress_apply(
    lambda x: [strip_n(verse, x["lyrics_sanitized_lang_lingua"]) for verse in x["verses_lower_rmp"]],
    axis=1,
)

  0%|          | 0/1259329 [00:00<?, ?it/s]

100%|██████████| 1259329/1259329 [01:30<00:00, 13968.60it/s]


In [20]:
for song in lyrics_distinct_all.sample(10).to_dict(orient="records"):
    print(song["track"], "\n")
    for verse, verse_n in zip(song["verses_lower"], song["verses_lower_strip_n"]):
        print(verse)
        print(verse_n)
    print("-" * 80)

Love To Hate You 

for seven months and fifteen days
i've been telling you lies in different ways
i know things will change
but i don't know when
you keep talking about us
like we still were friends
for seven months and fifteen days i've been telling you lies in different ways i know things will change but i don't know when you keep talking about us like we still were friends
i just hate the way you talk to me
i just love to say what's bothering me
i just hate the way you talk to me i just love to say what's bothering me
i love to hate you
i really love to hate you
and nothing you do
will ever change my mind
i'm doing fine
without you
i love to hate you i really love to hate you and nothing you do will ever change my mind i'm doing fine without you
it wasn't meant to be like this
all you gave her was one little innocent kiss
i didn't believe
she would turn to be
the love of your life
just like me
it wasn't meant to be like this all you gave her was one little innocent kiss i didn't bel

In [21]:

lyrics_distinct_all["lines"] = lyrics_distinct_all["lyrics_sanitized"].apply(
    lambda x: [line for line in x.split("\n") if line != ""]
)
# lower
lyrics_distinct_all["lines_lower"] = lyrics_distinct_all["lyrics_sanitized_lower"].apply(
    lambda x: [line for line in x.split("\n") if line != ""]
)
# remove punctuation
lyrics_distinct_all["lines_rmp"] = lyrics_distinct_all["lyrics_sanitized_rmp"].apply(
    lambda x: [line for line in x.split("\n") if line != ""]
)
lyrics_distinct_all["lines_lower_rmp"] = lyrics_distinct_all["lyrics_sanitized_lower_rmp"].apply(
    lambda x: [line for line in x.split("\n") if line != ""]
)

In [22]:
for song in lyrics_distinct_all.sample(10).to_dict(orient="records"):
    print(song["track"], "\n")
    for line in song["lines_lower"]:
        # raw print
        print(line)
    print("-" * 80)

Ruthie Lingle 

blue ruthie lingle, take me home
sad-eyed suzanna, take me home
the curse of those red lips all on me
goddess samantha, take me home
black-eyed rebecca, take me home
here, buxom gretta, take me home
legs, thighs, and navel, you're the only one
leah samantha, take me home
meek mother mary, take me home
sweet sister sarah, take me home
underneath the floorboards, down here eating dirt
seduce me, samantha, take me home
--------------------------------------------------------------------------------
Last You Heard Of Me 

found myself down at the alibi
for the second time this year
wrote my song down, gave it to the guy
then went to grab another beer
sonia's going to the parking lot
probably gonna smoke some weed
i'd go with, but i don't touch the stuff
unless i wanna go to sleep
you step outside to have a cigarette
as smokers crowd into the street
digging through your purse for matches
when, for a second, our eyes meet
and in the moment, i see everything
start to finish, s

## Split

In [23]:
# drop tag-language combinations with less than 10 songs
drop_tag_langs = lyrics_distinct_all.groupby(["primary_tag_genius", "lyrics_sanitized_lang_lingua"]).filter(
    lambda x: len(x) < 10
)[["primary_tag_genius", "lyrics_sanitized_lang_lingua"]]

lyrics_distinct_filtered = lyrics_distinct_all[
    ~lyrics_distinct_all.set_index(["primary_tag_genius", "lyrics_sanitized_lang_lingua"]).index.isin(
        drop_tag_langs.set_index(["primary_tag_genius", "lyrics_sanitized_lang_lingua"]).index
    )
]

In [24]:
lyrics_distinct_filtered[["primary_tag_genius", "lyrics_sanitized_lang_lingua"]].value_counts()

primary_tag_genius  lyrics_sanitized_lang_lingua
pop                 en                              716535
rock                en                              321692
rap                 en                              127443
r-b                 en                               38139
country             en                               35988
                                                     ...  
varnell-15-16-12th  en                                  11
r-b                 la                                  10
pop                 tr                                  10
                    ca                                  10
non-music           de                                  10
Name: count, Length: 86, dtype: int64

In [25]:
# stratify by language
from sklearn.model_selection import train_test_split

stratify = lyrics_distinct_filtered[["primary_tag_genius", "lyrics_sanitized_lang_lingua"]]
lyrics_train, lyrics_test = train_test_split(
    lyrics_distinct_filtered, test_size=0.3, stratify=stratify, random_state=42
)

In [26]:
lyrics_train[["primary_tag_genius", "lyrics_sanitized_lang_lingua"]].value_counts(ascending=True)

primary_tag_genius  lyrics_sanitized_lang_lingua
non-music           de                                   7
r-b                 la                                   7
pop                 ca                                   7
                    tr                                   7
                    vi                                   8
                                                     ...  
country             en                               25192
r-b                 en                               26697
rap                 en                               89210
rock                en                              225184
pop                 en                              501574
Name: count, Length: 86, dtype: int64

In [27]:
lyrics_test[["primary_tag_genius", "lyrics_sanitized_lang_lingua"]].value_counts(ascending=False)[:20]

primary_tag_genius  lyrics_sanitized_lang_lingua
pop                 en                              214961
rock                en                               96508
rap                 en                               38233
r-b                 en                               11442
country             en                               10796
non-music           en                                3827
pop                 yo                                 219
                    fr                                 125
                    sn                                 119
                    es                                 119
                    de                                 112
                    la                                  83
                    ja                                  73
denmark             en                                  68
pop                 tl                                  66
                    it                                  59
       

In [28]:
# save in this format with torch.save
# eval data in the format:
# {
#    df[]"lyrics_sanitized_lang_lingua"]: {
#        "sentence": {
#            df["primary_tag_genius"]: {
#                 "meta": {
#                     "train_data": ["train sentence 1", "train sentence 2"]
#                 },
#                 "data": ["test sentence 1", "test sentence 2"]
#            }
#        }
#    }
# }

In [29]:
import torch

In [30]:
def create_eval_lines_structure(lyrics_train, lyrics_test, lang_column, genre_column, lines_column, max_songs=10_000):
    """
    Creates a structured dictionary similar to eval_lines from given train and test DataFrames.

    :param lyrics_train: DataFrame containing the training data.
    :param lyrics_test: DataFrame containing the testing data.
    :param lang_column: Column name for language.
    :param genre_column: Column name for genre.
    :param lines_column: Column name for the lines to be aggregated.
    :return: A dictionary structured similarly to eval_lines.
    """
    # Add a column to distinguish between train and test data
    lyrics_train["type"] = "train"
    lyrics_test["type"] = "test"

    # Concatenate the train and test dataframes
    lyrics_combined = pd.concat([lyrics_train, lyrics_test])

    # Function to aggregate lines
    def aggregate_lines(data):
        return [line for song_lines in data[lines_column] for line in song_lines]

    # Group by language, genre, and type and aggregate lines
    aggregated_lines = (
        lyrics_combined.groupby([lang_column, genre_column, "type"])
        .apply(aggregate_lines)
        .reset_index(name=lines_column)
    )

    # Initialize eval_lines structure
    eval_lines = {}

    # Fill the eval_lines structure
    for _, row in aggregated_lines.iterrows():
        lang = row[lang_column]
        genre = row[genre_column]
        line_type = row["type"]
        lines = row[lines_column]

        if lang not in eval_lines:
            eval_lines[lang] = {}
        if "sentence" not in eval_lines[lang]:
            eval_lines[lang]["sentence"] = {}
        if genre not in eval_lines[lang]["sentence"]:
            eval_lines[lang]["sentence"][genre] = {"meta": {}, "data": []}
        if line_type == "train":
            eval_lines[lang]["sentence"][genre]["meta"]["train_data"] = lines[:max_songs]
        else:
            eval_lines[lang]["sentence"][genre]["data"] = lines[:max_songs]

    return eval_lines

In [31]:
eval_lines = create_eval_lines_structure(
    lyrics_train, lyrics_test, "lyrics_sanitized_lang_lingua", "primary_tag_genius", "lines"
)
torch.save(eval_lines, "data/lyrics_lines.pt")

In [32]:
eval_lines_lower = create_eval_lines_structure(
    lyrics_train, lyrics_test, "lyrics_sanitized_lang_lingua", "primary_tag_genius", "lines_lower"
)
torch.save(eval_lines_lower, "data/lyrics_lines_lower.pt")

In [33]:
eval_verses_strip_n = create_eval_lines_structure(
    lyrics_train, lyrics_test, "lyrics_sanitized_lang_lingua", "primary_tag_genius", "verses_strip_n"
)
torch.save(eval_verses_strip_n, "data/lyrics_verses_strip_n.pt")

In [34]:
eval_verses_lower_strip_n = create_eval_lines_structure(
    lyrics_train, lyrics_test, "lyrics_sanitized_lang_lingua", "primary_tag_genius", "verses_lower_strip_n"
)
torch.save(eval_verses_lower_strip_n, "data/lyrics_verses_lower_strip_n.pt")

In [35]:
eval_lines_rmp = create_eval_lines_structure(
    lyrics_train, lyrics_test, "lyrics_sanitized_lang_lingua", "primary_tag_genius", "lines_rmp"
)
torch.save(eval_lines_rmp, "data/lyrics_lines_rmp.pt")

In [36]:
eval_lines_rmp_lower = create_eval_lines_structure(
    lyrics_train, lyrics_test, "lyrics_sanitized_lang_lingua", "primary_tag_genius", "lines_lower_rmp"
)
torch.save(eval_lines_rmp_lower, "data/lyrics_lines_rmp_lower.pt")

In [37]:
eval_verses_rmp_strip_n = create_eval_lines_structure(
    lyrics_train, lyrics_test, "lyrics_sanitized_lang_lingua", "primary_tag_genius", "verses_rmp_strip_n"
)
torch.save(eval_verses_rmp_strip_n, "data/lyrics_verses_rmp_strip_n.pt")

In [38]:
eval_verses_rmp_lower_strip_n = create_eval_lines_structure(
    lyrics_train, lyrics_test, "lyrics_sanitized_lang_lingua", "primary_tag_genius", "verses_lower_rmp_strip_n"
)
torch.save(eval_verses_rmp_lower_strip_n, "data/lyrics_verses_rmp_lower_strip_n.pt")

In [39]:
eval_lines_rmp_lower["de"]

{'sentence': {'non-music': {'meta': {'train_data': ['this is the end of everything',
     'fallen und nicht aufgefangen werden',
     'mittelhochdeutsch',
     'uf dem anger',
     'were diu werlt alle min',
     'von deme mere unze an den rin',
     'des wolt ih mih darben',
     'daz diu chünegin von engellant',
     'lege an minen armen hei',
     'english',
     'on the green',
     'if all the world were mine',
     'from the sea to the rhine',
     'i would do without it',
     'if the queen of england',
     'would lie in my arms hey',
     'hier ist der westdeutsche rundfunk mit den nachrichten',
     'fünfzig atomkraftwerke sollen in der bundesrepublik',
     'in den nächsten zehn jahren errichtet werden',
     'jedes einzelne kann eine millionenstadt mit strom versorgen',
     'english translation',
     'here is the west german broadcasting station with the news',
     'fifty nuclear power stations will be built in the west german republic',
     'in the next ten years',
   

In [46]:
eval_verses_rmp_lower_strip_n["yo"]

{'sentence': {'non-music': {'meta': {'train_data': ['amudo nunchi mot chaegekkeum neoreul humchyeo boneun ge nae beoreusi doeeotgo gakkeum neowa nuni majuchil ttaemyeon amureochi anheun yeongil haneun baeuga doeeosseo action daetteum neoege gaseo mareul geonnaeneun sangsangdo yeoreo beon haebwa geunde wae nan neul neoga nae apeman omyeon eoreo beorineun geolkka i dont know why girl o nae heeoseutaildo dareun namjadeulboda gwaenchanko eoje saero san syeocheu saeksangdo pureun haneulgwa wanbyeokhan dekalkomani oneureun nae jajonsimeul kkeokkgo neoege gobaekhago sipjiman swipji anchi nan geujeo meonghani dareun goseul barabwa',
     'beautiful girl nae gyeoteseo utgo inneun niga neomu joha nuni busin geol areumdaun neol humchil su itge neoreul wonhae cause you are my',
     'ooh special ooh special ooh special special special girl ooh special ooh special ooh special special special girl',
     'neoreul bol su inneun chanseu wolhwasumokgeum naega wonhaneun geoneun jumariraneun boneoseu nar

In [41]:
with open("data/lyrics_langs.csv", "w") as f:
    # save to csv: l1, l2, ...
    f.write(",".join(lyrics_train["lyrics_sanitized_lang_lingua"].unique()))

In [42]:
# TODO: remove trailing punct chars, newlines, whitespace, etc.?
# TODO: double-check eval_verses_strip_n

In [43]:
eval_lines_lower

{'ca': {'sentence': {'pop': {'meta': {'train_data': ["ab votz d'angel",
      "lengu'espena, non bleza",
      'ab motz sotils',
      "plans plus c'obra d'engles",
      'ben assetatz',
      'ben ditz e sens repreza',
      'miels escoutatz',
      'ses tossir, que apres',
      'ab plans, sanglotz',
      'mostran la via',
      'de jhesu-crist',
      'que quex deuria',
      'tener, com el per',
      'nos la volc tener',
      'van prezican com',
      'ouescam dieu vezer ...',
      'religios',
      "fon li premieir'enpreza",
      'per gent que treu',
      'ni bruida non volgues',
      'mas jacopin',
      "apres manjar n'an queza",
      'ans desputan',
      'del vin cals mieillers es',
      'et an de plaitz',
      'cort establia',
      'et es vaudes',
      "qui'ls ne desvia:",
      "et los secretz d'ome",
      'volon saber',
      'per tal que',
      'miels si puescan far temer',
      'esperitals',
      'non es la lur paubreza:',
      'gardan lo lor',
      'pre

# Verse Labeling

In [44]:
labeled_parts = lyrics_distinct_all.loc[
    (lyrics_distinct_all["lyrics"].str.contains("verse|Verse"))
    & (lyrics_distinct_all["lyrics"].str.contains("chorus|Chorus"))
]

In [45]:
for i, row in labeled_parts.iterrows():
    print(row["lyrics"])
    print()
    if i > 100:
        break

!-Lyrics Begin-

[Verse 1:]
Well I know just what it is you want the way you love and get enough and then you move on
You play the game of who you need and learn his name and walk away to find the next one
You say the things your looking for look past me and door to door
But darling did you think I wouldn't know

[Chorus:]
I might not be what you want
I'm gonna be your halfway
I might not be what you need
But I'm gonna be the way
I'm never gonna be the thing you want
But I'm gonna be your halfway
I might not be what you need
I'm gonna be your halfway
(halfway, I'll be your halfway, halfway, I'll be your halfway)

[Verse 2:]
You like to close your eyes and nod and picture him and what he'd say and what he looks like
But all I can think is all the dreams in the world that can match up to the real thing, the real thing

[Chorus:]
I might not be what you want
I'm gonna be your halfway
I might not be what you need
But I'm gonna be the way
I'm never gonna be the thing you want
But I'm gonna 